## Information Integration and Analytic Data Processing
### Marcos Torres, nº62746


In [1]:
import pandas as pd
import numpy as np
from ydata_profiling import ProfileReport
import random
from astropy.coordinates import SkyCoord
import astropy.units as units
import networkx as nx 
from scipy.spatial.distance import pdist, squareform
from sklearn.metrics.pairwise import haversine_distances
from joblib import Parallel, delayed
from collections import defaultdict
from rapidfuzz import fuzz

In [2]:
import warnings
warnings.filterwarnings("ignore")


## Satellite Data Analysis: TESS, ALMA, HAWKI and JWST
### Individual Challenge: Data Cleaning Expert


For the purpose of this individual challenge, the dataset corresponding to the observations of the Transiting Exoplanet Survey Satellite (TESS), was duplicated to have it's records modified for the sake creating new data quality issues, not present in the original dataset.

In [3]:
tess = pd.read_csv(r'./Datasets/tessqueries.csv')
tess


intentType obs_collection provenance_name instrument_name project  \
0       science           TESS            SPOC      Photometer    TESS   
1       science           TESS            SPOC      Photometer    TESS   
2       science           TESS            SPOC      Photometer    TESS   
3       science           TESS            SPOC      Photometer    TESS   
4       science           TESS            SPOC      Photometer    TESS   
...         ...            ...             ...             ...     ...   
1403    science           TESS            SPOC      Photometer    TESS   
1404    science           TESS            SPOC      Photometer    TESS   
1405    science           TESS            SPOC      Photometer    TESS   
1406    science           TESS            SPOC      Photometer    TESS   
1407    science           TESS            SPOC      Photometer    TESS   

     filters wavelength_region target_name  target_classification  \
0       TESS           Optical    TESS FFI                    NaN   
1       TESS           Optical    TESS FFI                    NaN   
2       TESS           Optical    TESS FFI                    NaN   
3       TESS           Optical    TESS FFI                    NaN   
4       TESS           Optical    TESS FFI                    NaN   
...      ...               ...         ...                    ...   
1403    TESS           Optical    TESS FFI                    NaN   
1404    TESS           Optical    TESS FFI                    NaN   
1405    TESS           Optical    TESS FFI                    NaN   
1406    TESS           Optical    TESS FFI                    NaN   
1407    TESS           Optical    TESS FFI                    NaN   

              obs_id  ...  proposal_type  sequence_number  \
0     tess-s0086-1-1  ...            NaN               86   
1     tess-s0086-1-2  ...            NaN               86   
2     tess-s0086-1-3  ...            NaN               86   
3     tess-s0086-1-4  ...            NaN               86   
4     tess-s0086-2-1  ...            NaN               86   
...              ...  ...            ...              ...   
1403  tess-s0088-3-4  ...            NaN               88   
1404  tess-s0088-4-1  ...            NaN               88   
1405  tess-s0088-4-2  ...            NaN               88   
1406  tess-s0088-4-3  ...            NaN               88   
1407  tess-s0088-4-4  ...            NaN               88   

                                               s_region jpegURL  dataURL  \
0     POLYGON 84.397259 54.220049 84.340478 42.73188...     NaN      NaN   
1     POLYGON 64.081165 53.379423 67.62671 41.711452...     NaN      NaN   
2     POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
3     POLYGON 70.29962 29.735295 67.909289 41.484483...     NaN      NaN   
4     POLYGON 95.427814 77.267546 87.798089 66.01251...     NaN      NaN   
...                                                 ...     ...      ...   
1403  POLYGON 103.995769 -58.278586 111.769394 -47.3...     NaN      NaN   
1404  POLYGON 126.593612 -61.814511 124.108074 -73.2...     NaN      NaN   
1405  POLYGON 103.675924 -58.111101 89.215174 -68.14...     NaN      NaN   
1406  POLYGON 48.343253 -63.919623 70.359333 -59.102...     NaN      NaN   
1407  POLYGON 57.070484 -75.528303 89.037206 -68.474...     NaN      NaN   

      dataRights  mtFlag  srcDen      obsid      objID  
0         PUBLIC   False     NaN  236870228  700694124  
1         PUBLIC   False     NaN  236870229  700703621  
2         PUBLIC   False     NaN  236870242  700713800  
3         PUBLIC   False     NaN  236870243  700721420  
4         PUBLIC   False     NaN  236870245  700730556  
...          ...     ...     ...        ...        ...  
1403      PUBLIC   False     NaN  247910493  732056593  
1404      PUBLIC   False     NaN  247913721  732067225  
1405      PUBLIC   False     NaN  247916479  732076216  
1406      PUBLIC   False     NaN  247919459  732085054  
1407      PUBL

In [4]:
# Initial Profiling Tess
tess_profile = ProfileReport(tess, title="TESS", explorative=True)
tess_profile.to_file("tess_queries.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 33/33 [00:00<00:00, 65.49it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [5]:
tess_profile

While this was already observed in the main project, the dataset is extremely clean, the only noticeable issue being a few empty columns that are easily removable, as they do not correspond to anything relevant to the project's objectives.

With that in mind the following data quality issues were intentionally created through record manipulation:

-Misspellings

-Missing values in non-empty columns

-Value misfielding (Values being swapped between columns)

-Numeric columns having non-numerical data (For simplicity it was considered to replace with a manual N/A)

-Duplicate rows





AI was used to assist in coding process.


In [6]:

cols = list(tess.columns) #This allows to use the column names directly for each function


def random_misspell(word, char, pos): #A secondary function to the insert_misspellings function
    if len(word) > 1:
        return word[:pos] + char + word[pos + 1:] #through index slicing, the character defined in pos is replaced with something else
    return word

def introduce_missing_value(df,col,row_indices): # Introduce missing values
    df_copy = df.copy()
    for idx in row_indices:
        df_copy.loc[idx, col] = np.nan
    return df_copy

def introduce_misspellings(df,col,row_indices): # Introduce misspellings in string columns (this function affects the third character)
    df_copy = df.copy()
    shared_char = random.choice('abcdefghijklmnopqrstuvwxyz') 
    #This line selects a random character for the misspell function, being here ensures that only one character is selected for insertion in all the rows from the selected index
    for idx in row_indices:
        value = df_copy.loc[idx, col]
        if pd.notna(value):
            df_copy.loc[idx, col] = random_misspell(str(value),shared_char,3) #it will change the third character
    return df_copy

def introduce_misfield(df,col1,col2,row_indices): # Introduce misfielded values (swapping values between columns)
    df_copy = df.copy()
    for idx in row_indices: 
        df_copy.at[idx, col1], df_copy.at[idx, col2] = df_copy.at[idx, col2], df_copy.at[idx, col1]
    return df_copy


def introduce_wrong_data_type(df,col,row_indices): # Introduce wrong data types (random strings in numeric columns)
        df_copy = df.copy()
        WrongValue=str('N/A')
        for idx in row_indices: 
            df_copy.loc[idx, col] = WrongValue
        return df_copy

def duplicate_rows(df, row_indices): #Duplicate the selected row index or indices (this function creates 10 duplicates)
    df_copy = df.copy()
    duplicated_rows = df_copy.loc[np.repeat(row_indices, 10)]
    df_copy = pd.concat([df_copy, duplicated_rows], ignore_index=True)
    return df_copy


One possible mistake that could happen while adding data to a dataset or database is that some column values, like for an example, those corresponding to the minimum and maximum electromagnetic range of the observations, end up swapped.

In [7]:

rows1=tess.index[6:25].tolist()
dirtyTess=introduce_misfield(tess,cols[18],cols[19],rows1)
dirtyTess

intentType obs_collection provenance_name instrument_name project  \
0       science           TESS            SPOC      Photometer    TESS   
1       science           TESS            SPOC      Photometer    TESS   
2       science           TESS            SPOC      Photometer    TESS   
3       science           TESS            SPOC      Photometer    TESS   
4       science           TESS            SPOC      Photometer    TESS   
...         ...            ...             ...             ...     ...   
1403    science           TESS            SPOC      Photometer    TESS   
1404    science           TESS            SPOC      Photometer    TESS   
1405    science           TESS            SPOC      Photometer    TESS   
1406    science           TESS            SPOC      Photometer    TESS   
1407    science           TESS            SPOC      Photometer    TESS   

     filters wavelength_region target_name  target_classification  \
0       TESS           Optical    TESS FFI                    NaN   
1       TESS           Optical    TESS FFI                    NaN   
2       TESS           Optical    TESS FFI                    NaN   
3       TESS           Optical    TESS FFI                    NaN   
4       TESS           Optical    TESS FFI                    NaN   
...      ...               ...         ...                    ...   
1403    TESS           Optical    TESS FFI                    NaN   
1404    TESS           Optical    TESS FFI                    NaN   
1405    TESS           Optical    TESS FFI                    NaN   
1406    TESS           Optical    TESS FFI                    NaN   
1407    TESS           Optical    TESS FFI                    NaN   

              obs_id  ...  proposal_type  sequence_number  \
0     tess-s0086-1-1  ...            NaN               86   
1     tess-s0086-1-2  ...            NaN               86   
2     tess-s0086-1-3  ...            NaN               86   
3     tess-s0086-1-4  ...            NaN               86   
4     tess-s0086-2-1  ...            NaN               86   
...              ...  ...            ...              ...   
1403  tess-s0088-3-4  ...            NaN               88   
1404  tess-s0088-4-1  ...            NaN               88   
1405  tess-s0088-4-2  ...            NaN               88   
1406  tess-s0088-4-3  ...            NaN               88   
1407  tess-s0088-4-4  ...            NaN               88   

                                               s_region jpegURL  dataURL  \
0     POLYGON 84.397259 54.220049 84.340478 42.73188...     NaN      NaN   
1     POLYGON 64.081165 53.379423 67.62671 41.711452...     NaN      NaN   
2     POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
3     POLYGON 70.29962 29.735295 67.909289 41.484483...     NaN      NaN   
4     POLYGON 95.427814 77.267546 87.798089 66.01251...     NaN      NaN   
...                                                 ...     ...      ...   
1403  POLYGON 103.995769 -58.278586 111.769394 -47.3...     NaN      NaN   
1404  POLYGON 126.593612 -61.814511 124.108074 -73.2...     NaN      NaN   
1405  POLYGON 103.675924 -58.111101 89.215174 -68.14...     NaN      NaN   
1406  POLYGON 48.343253 -63.919623 70.359333 -59.102...     NaN      NaN   
1407  POLYGON 57.070484 -75.528303 89.037206 -68.474...     NaN      NaN   

      dataRights  mtFlag  srcDen      obsid      objID  
0         PUBLIC   False     NaN  236870228  700694124  
1         PUBLIC   False     NaN  236870229  700703621  
2         PUBLIC   False     NaN  236870242  700713800  
3         PUBLIC   False     NaN  236870243  700721420  
4         PUBLIC   False     NaN  236870245  700730556  
...          ...     ...     ...        ...        ...  
1403      PUBLIC   False     NaN  247910493  732056593  
1404      PUBLIC   False     NaN  247913721  732067225  
1405      PUBLIC   False     NaN  247916479  732076216  
1406      PUBLIC   False     NaN  247919459  732085054  
1407      PUBL

A lot of datasets contain columns with a single unique value, however if these values are added manually, there is a possiblity of misspellings, and if the process of populating said columns is automated, this can generate several misspelled rows.

In [8]:
rows2=tess.index[1:9].tolist()
dirtyTess2=introduce_misspellings(dirtyTess,cols[2],rows2)
dirtyTess2

intentType obs_collection provenance_name instrument_name project  \
0       science           TESS            SPOC      Photometer    TESS   
1       science           TESS            SPOa      Photometer    TESS   
2       science           TESS            SPOa      Photometer    TESS   
3       science           TESS            SPOa      Photometer    TESS   
4       science           TESS            SPOa      Photometer    TESS   
...         ...            ...             ...             ...     ...   
1403    science           TESS            SPOC      Photometer    TESS   
1404    science           TESS            SPOC      Photometer    TESS   
1405    science           TESS            SPOC      Photometer    TESS   
1406    science           TESS            SPOC      Photometer    TESS   
1407    science           TESS            SPOC      Photometer    TESS   

     filters wavelength_region target_name  target_classification  \
0       TESS           Optical    TESS FFI                    NaN   
1       TESS           Optical    TESS FFI                    NaN   
2       TESS           Optical    TESS FFI                    NaN   
3       TESS           Optical    TESS FFI                    NaN   
4       TESS           Optical    TESS FFI                    NaN   
...      ...               ...         ...                    ...   
1403    TESS           Optical    TESS FFI                    NaN   
1404    TESS           Optical    TESS FFI                    NaN   
1405    TESS           Optical    TESS FFI                    NaN   
1406    TESS           Optical    TESS FFI                    NaN   
1407    TESS           Optical    TESS FFI                    NaN   

              obs_id  ...  proposal_type  sequence_number  \
0     tess-s0086-1-1  ...            NaN               86   
1     tess-s0086-1-2  ...            NaN               86   
2     tess-s0086-1-3  ...            NaN               86   
3     tess-s0086-1-4  ...            NaN               86   
4     tess-s0086-2-1  ...            NaN               86   
...              ...  ...            ...              ...   
1403  tess-s0088-3-4  ...            NaN               88   
1404  tess-s0088-4-1  ...            NaN               88   
1405  tess-s0088-4-2  ...            NaN               88   
1406  tess-s0088-4-3  ...            NaN               88   
1407  tess-s0088-4-4  ...            NaN               88   

                                               s_region jpegURL  dataURL  \
0     POLYGON 84.397259 54.220049 84.340478 42.73188...     NaN      NaN   
1     POLYGON 64.081165 53.379423 67.62671 41.711452...     NaN      NaN   
2     POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
3     POLYGON 70.29962 29.735295 67.909289 41.484483...     NaN      NaN   
4     POLYGON 95.427814 77.267546 87.798089 66.01251...     NaN      NaN   
...                                                 ...     ...      ...   
1403  POLYGON 103.995769 -58.278586 111.769394 -47.3...     NaN      NaN   
1404  POLYGON 126.593612 -61.814511 124.108074 -73.2...     NaN      NaN   
1405  POLYGON 103.675924 -58.111101 89.215174 -68.14...     NaN      NaN   
1406  POLYGON 48.343253 -63.919623 70.359333 -59.102...     NaN      NaN   
1407  POLYGON 57.070484 -75.528303 89.037206 -68.474...     NaN      NaN   

      dataRights  mtFlag  srcDen      obsid      objID  
0         PUBLIC   False     NaN  236870228  700694124  
1         PUBLIC   False     NaN  236870229  700703621  
2         PUBLIC   False     NaN  236870242  700713800  
3         PUBLIC   False     NaN  236870243  700721420  
4         PUBLIC   False     NaN  236870245  700730556  
...          ...     ...     ...        ...        ...  
1403      PUBLIC   False     NaN  247910493  732056593  
1404      PUBLIC   False     NaN  247913721  732067225  
1405      PUBLIC   False     NaN  247916479  732076216  
1406      PUBLIC   False     NaN  247919459  732085054  
1407      PUBL

Data can come from different sources, and some may choose to manually indicate a missing value with the string N/A, instead of simply leaving the value empty, regardless of it being a numeric column or not, which can cause issues later down the line.

In [9]:
rows3=tess.index[10:50].tolist()
dirtyTess3=introduce_wrong_data_type(dirtyTess2,cols[10],rows3)
dirtyTess3

intentType obs_collection provenance_name instrument_name project  \
0       science           TESS            SPOC      Photometer    TESS   
1       science           TESS            SPOa      Photometer    TESS   
2       science           TESS            SPOa      Photometer    TESS   
3       science           TESS            SPOa      Photometer    TESS   
4       science           TESS            SPOa      Photometer    TESS   
...         ...            ...             ...             ...     ...   
1403    science           TESS            SPOC      Photometer    TESS   
1404    science           TESS            SPOC      Photometer    TESS   
1405    science           TESS            SPOC      Photometer    TESS   
1406    science           TESS            SPOC      Photometer    TESS   
1407    science           TESS            SPOC      Photometer    TESS   

     filters wavelength_region target_name  target_classification  \
0       TESS           Optical    TESS FFI                    NaN   
1       TESS           Optical    TESS FFI                    NaN   
2       TESS           Optical    TESS FFI                    NaN   
3       TESS           Optical    TESS FFI                    NaN   
4       TESS           Optical    TESS FFI                    NaN   
...      ...               ...         ...                    ...   
1403    TESS           Optical    TESS FFI                    NaN   
1404    TESS           Optical    TESS FFI                    NaN   
1405    TESS           Optical    TESS FFI                    NaN   
1406    TESS           Optical    TESS FFI                    NaN   
1407    TESS           Optical    TESS FFI                    NaN   

              obs_id  ... proposal_type  sequence_number  \
0     tess-s0086-1-1  ...           NaN               86   
1     tess-s0086-1-2  ...           NaN               86   
2     tess-s0086-1-3  ...           NaN               86   
3     tess-s0086-1-4  ...           NaN               86   
4     tess-s0086-2-1  ...           NaN               86   
...              ...  ...           ...              ...   
1403  tess-s0088-3-4  ...           NaN               88   
1404  tess-s0088-4-1  ...           NaN               88   
1405  tess-s0088-4-2  ...           NaN               88   
1406  tess-s0088-4-3  ...           NaN               88   
1407  tess-s0088-4-4  ...           NaN               88   

                                               s_region jpegURL  dataURL  \
0     POLYGON 84.397259 54.220049 84.340478 42.73188...     NaN      NaN   
1     POLYGON 64.081165 53.379423 67.62671 41.711452...     NaN      NaN   
2     POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
3     POLYGON 70.29962 29.735295 67.909289 41.484483...     NaN      NaN   
4     POLYGON 95.427814 77.267546 87.798089 66.01251...     NaN      NaN   
...                                                 ...     ...      ...   
1403  POLYGON 103.995769 -58.278586 111.769394 -47.3...     NaN      NaN   
1404  POLYGON 126.593612 -61.814511 124.108074 -73.2...     NaN      NaN   
1405  POLYGON 103.675924 -58.111101 89.215174 -68.14...     NaN      NaN   
1406  POLYGON 48.343253 -63.919623 70.359333 -59.102...     NaN      NaN   
1407  POLYGON 57.070484 -75.528303 89.037206 -68.474...     NaN      NaN   

      dataRights  mtFlag  srcDen      obsid      objID  
0         PUBLIC   False     NaN  236870228  700694124  
1         PUBLIC   False     NaN  236870229  700703621  
2         PUBLIC   False     NaN  236870242  700713800  
3         PUBLIC   False     NaN  236870243  700721420  
4         PUBLIC   False     NaN  236870245  700730556  
...          ...     ...     ...        ...        ...  
1403      PUBLIC   False     NaN  247910493  732056593  
1404      PUBLIC   False     NaN  247913721  732067225  
1405      PUBLIC   False     NaN  247916479  732076216  
1406      PUBLIC   False     NaN  247919459  732085054  
1407      PUBLIC   False  

Another issue from joining data from several sources is the possibility of the sources containing common data, which can result in row duplicates.
In some cases it can be difficult to detect said duplicates, requiring the need of more elaborate rules of deduplication, although in this case, there are several columns that assign unique ID values, which makes the presence of duplicates more noticeable.



Unfortunately, a limitation with the code made the duplicated columns be appended at the tail of the dataframe, but the strategy to removing them remains the same.

In [10]:
rows4=[2] #Only one row used in this case
dirtyTess4=duplicate_rows(dirtyTess3,rows4)
dirtyTess4

intentType obs_collection provenance_name instrument_name project  \
0       science           TESS            SPOC      Photometer    TESS   
1       science           TESS            SPOa      Photometer    TESS   
2       science           TESS            SPOa      Photometer    TESS   
3       science           TESS            SPOa      Photometer    TESS   
4       science           TESS            SPOa      Photometer    TESS   
...         ...            ...             ...             ...     ...   
1413    science           TESS            SPOa      Photometer    TESS   
1414    science           TESS            SPOa      Photometer    TESS   
1415    science           TESS            SPOa      Photometer    TESS   
1416    science           TESS            SPOa      Photometer    TESS   
1417    science           TESS            SPOa      Photometer    TESS   

     filters wavelength_region target_name  target_classification  \
0       TESS           Optical    TESS FFI                    NaN   
1       TESS           Optical    TESS FFI                    NaN   
2       TESS           Optical    TESS FFI                    NaN   
3       TESS           Optical    TESS FFI                    NaN   
4       TESS           Optical    TESS FFI                    NaN   
...      ...               ...         ...                    ...   
1413    TESS           Optical    TESS FFI                    NaN   
1414    TESS           Optical    TESS FFI                    NaN   
1415    TESS           Optical    TESS FFI                    NaN   
1416    TESS           Optical    TESS FFI                    NaN   
1417    TESS           Optical    TESS FFI                    NaN   

              obs_id  ... proposal_type  sequence_number  \
0     tess-s0086-1-1  ...           NaN               86   
1     tess-s0086-1-2  ...           NaN               86   
2     tess-s0086-1-3  ...           NaN               86   
3     tess-s0086-1-4  ...           NaN               86   
4     tess-s0086-2-1  ...           NaN               86   
...              ...  ...           ...              ...   
1413  tess-s0086-1-3  ...           NaN               86   
1414  tess-s0086-1-3  ...           NaN               86   
1415  tess-s0086-1-3  ...           NaN               86   
1416  tess-s0086-1-3  ...           NaN               86   
1417  tess-s0086-1-3  ...           NaN               86   

                                               s_region jpegURL  dataURL  \
0     POLYGON 84.397259 54.220049 84.340478 42.73188...     NaN      NaN   
1     POLYGON 64.081165 53.379423 67.62671 41.711452...     NaN      NaN   
2     POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
3     POLYGON 70.29962 29.735295 67.909289 41.484483...     NaN      NaN   
4     POLYGON 95.427814 77.267546 87.798089 66.01251...     NaN      NaN   
...                                                 ...     ...      ...   
1413  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1414  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1415  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1416  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1417  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   

      dataRights  mtFlag  srcDen      obsid      objID  
0         PUBLIC   False     NaN  236870228  700694124  
1         PUBLIC   False     NaN  236870229  700703621  
2         PUBLIC   False     NaN  236870242  700713800  
3         PUBLIC   False     NaN  236870243  700721420  
4         PUBLIC   False     NaN  236870245  700730556  
...          ...     ...     ...        ...        ...  
1413      PUBLIC   False     NaN  236870242  700713800  
1414      PUBLIC   False     NaN  236870242  700713800  
1415      PUBLIC   False     NaN  236870242  700713800  
1416      PUBLIC   False     NaN  236870242  700713800  
1417      PUBLIC   False  

Finally, another important oversight, going from issue of wrong data types, is when there are actual empty rows in the column mixed with the ones containing the string 'N/A', which complicates cleaning.

In [11]:
rows5=tess.index[50:60].tolist() 
dirtyTess5=introduce_missing_value(dirtyTess4,cols[10],rows5)
dirtyTess5

intentType obs_collection provenance_name instrument_name project  \
0       science           TESS            SPOC      Photometer    TESS   
1       science           TESS            SPOa      Photometer    TESS   
2       science           TESS            SPOa      Photometer    TESS   
3       science           TESS            SPOa      Photometer    TESS   
4       science           TESS            SPOa      Photometer    TESS   
...         ...            ...             ...             ...     ...   
1413    science           TESS            SPOa      Photometer    TESS   
1414    science           TESS            SPOa      Photometer    TESS   
1415    science           TESS            SPOa      Photometer    TESS   
1416    science           TESS            SPOa      Photometer    TESS   
1417    science           TESS            SPOa      Photometer    TESS   

     filters wavelength_region target_name  target_classification  \
0       TESS           Optical    TESS FFI                    NaN   
1       TESS           Optical    TESS FFI                    NaN   
2       TESS           Optical    TESS FFI                    NaN   
3       TESS           Optical    TESS FFI                    NaN   
4       TESS           Optical    TESS FFI                    NaN   
...      ...               ...         ...                    ...   
1413    TESS           Optical    TESS FFI                    NaN   
1414    TESS           Optical    TESS FFI                    NaN   
1415    TESS           Optical    TESS FFI                    NaN   
1416    TESS           Optical    TESS FFI                    NaN   
1417    TESS           Optical    TESS FFI                    NaN   

              obs_id  ... proposal_type  sequence_number  \
0     tess-s0086-1-1  ...           NaN               86   
1     tess-s0086-1-2  ...           NaN               86   
2     tess-s0086-1-3  ...           NaN               86   
3     tess-s0086-1-4  ...           NaN               86   
4     tess-s0086-2-1  ...           NaN               86   
...              ...  ...           ...              ...   
1413  tess-s0086-1-3  ...           NaN               86   
1414  tess-s0086-1-3  ...           NaN               86   
1415  tess-s0086-1-3  ...           NaN               86   
1416  tess-s0086-1-3  ...           NaN               86   
1417  tess-s0086-1-3  ...           NaN               86   

                                               s_region jpegURL  dataURL  \
0     POLYGON 84.397259 54.220049 84.340478 42.73188...     NaN      NaN   
1     POLYGON 64.081165 53.379423 67.62671 41.711452...     NaN      NaN   
2     POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
3     POLYGON 70.29962 29.735295 67.909289 41.484483...     NaN      NaN   
4     POLYGON 95.427814 77.267546 87.798089 66.01251...     NaN      NaN   
...                                                 ...     ...      ...   
1413  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1414  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1415  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1416  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1417  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   

      dataRights  mtFlag  srcDen      obsid      objID  
0         PUBLIC   False     NaN  236870228  700694124  
1         PUBLIC   False     NaN  236870229  700703621  
2         PUBLIC   False     NaN  236870242  700713800  
3         PUBLIC   False     NaN  236870243  700721420  
4         PUBLIC   False     NaN  236870245  700730556  
...          ...     ...     ...        ...        ...  
1413      PUBLIC   False     NaN  236870242  700713800  
1414      PUBLIC   False     NaN  236870242  700713800  
1415      PUBLIC   False     NaN  236870242  700713800  
1416      PUBLIC   False     NaN  236870242  700713800  
1417      PUBLIC   False  

In [12]:
dirtyTess5.to_csv('DirtyTess.csv',index=True)

In [13]:
dirty_profile = ProfileReport(dirtyTess5, title="TESS (Dirty)", explorative=True)
dirty_profile.to_file("dirty_queries.html")

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 33/33 [00:00<00:00, 99.38it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Export report to file:   0%|          | 0/1 [00:00<?, ?it/s]

In [14]:
#dirty_profile

## Cleaning Procedures

Dealing with duplicate columns should be the first thing to do before attempting to do any other form of cleaning.

In [15]:
tess_cleanup=dirtyTess5.copy()
tess_cleanup

intentType obs_collection provenance_name instrument_name project  \
0       science           TESS            SPOC      Photometer    TESS   
1       science           TESS            SPOa      Photometer    TESS   
2       science           TESS            SPOa      Photometer    TESS   
3       science           TESS            SPOa      Photometer    TESS   
4       science           TESS            SPOa      Photometer    TESS   
...         ...            ...             ...             ...     ...   
1413    science           TESS            SPOa      Photometer    TESS   
1414    science           TESS            SPOa      Photometer    TESS   
1415    science           TESS            SPOa      Photometer    TESS   
1416    science           TESS            SPOa      Photometer    TESS   
1417    science           TESS            SPOa      Photometer    TESS   

     filters wavelength_region target_name  target_classification  \
0       TESS           Optical    TESS FFI                    NaN   
1       TESS           Optical    TESS FFI                    NaN   
2       TESS           Optical    TESS FFI                    NaN   
3       TESS           Optical    TESS FFI                    NaN   
4       TESS           Optical    TESS FFI                    NaN   
...      ...               ...         ...                    ...   
1413    TESS           Optical    TESS FFI                    NaN   
1414    TESS           Optical    TESS FFI                    NaN   
1415    TESS           Optical    TESS FFI                    NaN   
1416    TESS           Optical    TESS FFI                    NaN   
1417    TESS           Optical    TESS FFI                    NaN   

              obs_id  ... proposal_type  sequence_number  \
0     tess-s0086-1-1  ...           NaN               86   
1     tess-s0086-1-2  ...           NaN               86   
2     tess-s0086-1-3  ...           NaN               86   
3     tess-s0086-1-4  ...           NaN               86   
4     tess-s0086-2-1  ...           NaN               86   
...              ...  ...           ...              ...   
1413  tess-s0086-1-3  ...           NaN               86   
1414  tess-s0086-1-3  ...           NaN               86   
1415  tess-s0086-1-3  ...           NaN               86   
1416  tess-s0086-1-3  ...           NaN               86   
1417  tess-s0086-1-3  ...           NaN               86   

                                               s_region jpegURL  dataURL  \
0     POLYGON 84.397259 54.220049 84.340478 42.73188...     NaN      NaN   
1     POLYGON 64.081165 53.379423 67.62671 41.711452...     NaN      NaN   
2     POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
3     POLYGON 70.29962 29.735295 67.909289 41.484483...     NaN      NaN   
4     POLYGON 95.427814 77.267546 87.798089 66.01251...     NaN      NaN   
...                                                 ...     ...      ...   
1413  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1414  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1415  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1416  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1417  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   

      dataRights  mtFlag  srcDen      obsid      objID  
0         PUBLIC   False     NaN  236870228  700694124  
1         PUBLIC   False     NaN  236870229  700703621  
2         PUBLIC   False     NaN  236870242  700713800  
3         PUBLIC   False     NaN  236870243  700721420  
4         PUBLIC   False     NaN  236870245  700730556  
...          ...     ...     ...        ...        ...  
1413      PUBLIC   False     NaN  236870242  700713800  
1414      PUBLIC   False     NaN  236870242  700713800  
1415      PUBLIC   False     NaN  236870242  700713800  
1416      PUBLIC   False     NaN  236870242  700713800  
1417      PUBLIC   False  

If the issue was that specific column values were duplicated, then the solution would depend on which columns were affected.
Either requiring some form of ground truth for comparison, or removal if the absence of said rows doesn't cause a significant loss of data.

In [16]:
tess_cleanup.duplicated() #This function returns a Boolean column indicating of the row is a complete duplicate or not


0       False
1       False
2       False
3       False
4       False
        ...  
1413     True
1414     True
1415     True
1416     True
1417     True
Length: 1418, dtype: bool

In [17]:
tess_cleanup.drop_duplicates() #This quickly removes said rows

intentType obs_collection provenance_name instrument_name project  \
0       science           TESS            SPOC      Photometer    TESS   
1       science           TESS            SPOa      Photometer    TESS   
2       science           TESS            SPOa      Photometer    TESS   
3       science           TESS            SPOa      Photometer    TESS   
4       science           TESS            SPOa      Photometer    TESS   
...         ...            ...             ...             ...     ...   
1403    science           TESS            SPOC      Photometer    TESS   
1404    science           TESS            SPOC      Photometer    TESS   
1405    science           TESS            SPOC      Photometer    TESS   
1406    science           TESS            SPOC      Photometer    TESS   
1407    science           TESS            SPOC      Photometer    TESS   

     filters wavelength_region target_name  target_classification  \
0       TESS           Optical    TESS FFI                    NaN   
1       TESS           Optical    TESS FFI                    NaN   
2       TESS           Optical    TESS FFI                    NaN   
3       TESS           Optical    TESS FFI                    NaN   
4       TESS           Optical    TESS FFI                    NaN   
...      ...               ...         ...                    ...   
1403    TESS           Optical    TESS FFI                    NaN   
1404    TESS           Optical    TESS FFI                    NaN   
1405    TESS           Optical    TESS FFI                    NaN   
1406    TESS           Optical    TESS FFI                    NaN   
1407    TESS           Optical    TESS FFI                    NaN   

              obs_id  ... proposal_type  sequence_number  \
0     tess-s0086-1-1  ...           NaN               86   
1     tess-s0086-1-2  ...           NaN               86   
2     tess-s0086-1-3  ...           NaN               86   
3     tess-s0086-1-4  ...           NaN               86   
4     tess-s0086-2-1  ...           NaN               86   
...              ...  ...           ...              ...   
1403  tess-s0088-3-4  ...           NaN               88   
1404  tess-s0088-4-1  ...           NaN               88   
1405  tess-s0088-4-2  ...           NaN               88   
1406  tess-s0088-4-3  ...           NaN               88   
1407  tess-s0088-4-4  ...           NaN               88   

                                               s_region jpegURL  dataURL  \
0     POLYGON 84.397259 54.220049 84.340478 42.73188...     NaN      NaN   
1     POLYGON 64.081165 53.379423 67.62671 41.711452...     NaN      NaN   
2     POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
3     POLYGON 70.29962 29.735295 67.909289 41.484483...     NaN      NaN   
4     POLYGON 95.427814 77.267546 87.798089 66.01251...     NaN      NaN   
...                                                 ...     ...      ...   
1403  POLYGON 103.995769 -58.278586 111.769394 -47.3...     NaN      NaN   
1404  POLYGON 126.593612 -61.814511 124.108074 -73.2...     NaN      NaN   
1405  POLYGON 103.675924 -58.111101 89.215174 -68.14...     NaN      NaN   
1406  POLYGON 48.343253 -63.919623 70.359333 -59.102...     NaN      NaN   
1407  POLYGON 57.070484 -75.528303 89.037206 -68.474...     NaN      NaN   

      dataRights  mtFlag  srcDen      obsid      objID  
0         PUBLIC   False     NaN  236870228  700694124  
1         PUBLIC   False     NaN  236870229  700703621  
2         PUBLIC   False     NaN  236870242  700713800  
3         PUBLIC   False     NaN  236870243  700721420  
4         PUBLIC   False     NaN  236870245  700730556  
...          ...     ...     ...        ...        ...  
1403      PUBLIC   False     NaN  247910493  732056593  
1404      PUBLIC   False     NaN  247913721  732067225  
1405      PUBLIC   False     NaN  247916479  732076216  
1406      PUBLIC   False     NaN  247919459  732085054  
1407      PUBLIC   False  

Dealing with misspellings is easy if the word in question is already present and correctly written somewhere else.

In [18]:
tess_cleanup['provenance_name'] = str('SPOC')
tess_cleanup

intentType obs_collection provenance_name instrument_name project  \
0       science           TESS            SPOC      Photometer    TESS   
1       science           TESS            SPOC      Photometer    TESS   
2       science           TESS            SPOC      Photometer    TESS   
3       science           TESS            SPOC      Photometer    TESS   
4       science           TESS            SPOC      Photometer    TESS   
...         ...            ...             ...             ...     ...   
1413    science           TESS            SPOC      Photometer    TESS   
1414    science           TESS            SPOC      Photometer    TESS   
1415    science           TESS            SPOC      Photometer    TESS   
1416    science           TESS            SPOC      Photometer    TESS   
1417    science           TESS            SPOC      Photometer    TESS   

     filters wavelength_region target_name  target_classification  \
0       TESS           Optical    TESS FFI                    NaN   
1       TESS           Optical    TESS FFI                    NaN   
2       TESS           Optical    TESS FFI                    NaN   
3       TESS           Optical    TESS FFI                    NaN   
4       TESS           Optical    TESS FFI                    NaN   
...      ...               ...         ...                    ...   
1413    TESS           Optical    TESS FFI                    NaN   
1414    TESS           Optical    TESS FFI                    NaN   
1415    TESS           Optical    TESS FFI                    NaN   
1416    TESS           Optical    TESS FFI                    NaN   
1417    TESS           Optical    TESS FFI                    NaN   

              obs_id  ... proposal_type  sequence_number  \
0     tess-s0086-1-1  ...           NaN               86   
1     tess-s0086-1-2  ...           NaN               86   
2     tess-s0086-1-3  ...           NaN               86   
3     tess-s0086-1-4  ...           NaN               86   
4     tess-s0086-2-1  ...           NaN               86   
...              ...  ...           ...              ...   
1413  tess-s0086-1-3  ...           NaN               86   
1414  tess-s0086-1-3  ...           NaN               86   
1415  tess-s0086-1-3  ...           NaN               86   
1416  tess-s0086-1-3  ...           NaN               86   
1417  tess-s0086-1-3  ...           NaN               86   

                                               s_region jpegURL  dataURL  \
0     POLYGON 84.397259 54.220049 84.340478 42.73188...     NaN      NaN   
1     POLYGON 64.081165 53.379423 67.62671 41.711452...     NaN      NaN   
2     POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
3     POLYGON 70.29962 29.735295 67.909289 41.484483...     NaN      NaN   
4     POLYGON 95.427814 77.267546 87.798089 66.01251...     NaN      NaN   
...                                                 ...     ...      ...   
1413  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1414  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1415  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1416  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1417  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   

      dataRights  mtFlag  srcDen      obsid      objID  
0         PUBLIC   False     NaN  236870228  700694124  
1         PUBLIC   False     NaN  236870229  700703621  
2         PUBLIC   False     NaN  236870242  700713800  
3         PUBLIC   False     NaN  236870243  700721420  
4         PUBLIC   False     NaN  236870245  700730556  
...          ...     ...     ...        ...        ...  
1413      PUBLIC   False     NaN  236870242  700713800  
1414      PUBLIC   False     NaN  236870242  700713800  
1415      PUBLIC   False     NaN  236870242  700713800  
1416      PUBLIC   False     NaN  236870242  700713800  
1417      PUBLIC   False  

To deal with the issue of misfielding, taking into account the rest of the values present in both of the affected columns, it's possible to do it manually.

In [ ]:
id1=tess_cleanup.index[6:25].tolist()

col1='em_min'
col2='em_max'


for id in id1: 
    tess_cleanup.at[id, col1], tess_cleanup.at[id, col2] = tess_cleanup.at[id, col2], tess_cleanup.at[id, col1]


tess_cleanup

Since the column with both empty values and incorrect data types corresponds to coordinates, there is no direct way to deal with these errors, and since this is already a large dataset, removing them would not affect the data too severely.

In [21]:
tess_cleanup=tess_cleanup[tess_cleanup['s_ra'] != 'N/A']
tess_cleanup=tess_cleanup.dropna(subset=['s_ra'])
tess_cleanup

intentType obs_collection provenance_name instrument_name project  \
0       science           TESS            SPOC      Photometer    TESS   
1       science           TESS            SPOC      Photometer    TESS   
2       science           TESS            SPOC      Photometer    TESS   
3       science           TESS            SPOC      Photometer    TESS   
4       science           TESS            SPOC      Photometer    TESS   
...         ...            ...             ...             ...     ...   
1413    science           TESS            SPOC      Photometer    TESS   
1414    science           TESS            SPOC      Photometer    TESS   
1415    science           TESS            SPOC      Photometer    TESS   
1416    science           TESS            SPOC      Photometer    TESS   
1417    science           TESS            SPOC      Photometer    TESS   

     filters wavelength_region target_name  target_classification  \
0       TESS           Optical    TESS FFI                    NaN   
1       TESS           Optical    TESS FFI                    NaN   
2       TESS           Optical    TESS FFI                    NaN   
3       TESS           Optical    TESS FFI                    NaN   
4       TESS           Optical    TESS FFI                    NaN   
...      ...               ...         ...                    ...   
1413    TESS           Optical    TESS FFI                    NaN   
1414    TESS           Optical    TESS FFI                    NaN   
1415    TESS           Optical    TESS FFI                    NaN   
1416    TESS           Optical    TESS FFI                    NaN   
1417    TESS           Optical    TESS FFI                    NaN   

              obs_id  ... proposal_type  sequence_number  \
0     tess-s0086-1-1  ...           NaN               86   
1     tess-s0086-1-2  ...           NaN               86   
2     tess-s0086-1-3  ...           NaN               86   
3     tess-s0086-1-4  ...           NaN               86   
4     tess-s0086-2-1  ...           NaN               86   
...              ...  ...           ...              ...   
1413  tess-s0086-1-3  ...           NaN               86   
1414  tess-s0086-1-3  ...           NaN               86   
1415  tess-s0086-1-3  ...           NaN               86   
1416  tess-s0086-1-3  ...           NaN               86   
1417  tess-s0086-1-3  ...           NaN               86   

                                               s_region jpegURL  dataURL  \
0     POLYGON 84.397259 54.220049 84.340478 42.73188...     NaN      NaN   
1     POLYGON 64.081165 53.379423 67.62671 41.711452...     NaN      NaN   
2     POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
3     POLYGON 70.29962 29.735295 67.909289 41.484483...     NaN      NaN   
4     POLYGON 95.427814 77.267546 87.798089 66.01251...     NaN      NaN   
...                                                 ...     ...      ...   
1413  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1414  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1415  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1416  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   
1417  POLYGON 56.900467 27.410355 52.298245 38.23203...     NaN      NaN   

      dataRights  mtFlag  srcDen      obsid      objID  
0         PUBLIC   False     NaN  236870228  700694124  
1         PUBLIC   False     NaN  236870229  700703621  
2         PUBLIC   False     NaN  236870242  700713800  
3         PUBLIC   False     NaN  236870243  700721420  
4         PUBLIC   False     NaN  236870245  700730556  
...          ...     ...     ...        ...        ...  
1413      PUBLIC   False     NaN  236870242  700713800  
1414      PUBLIC   False     NaN  236870242  700713800  
1415      PUBLIC   False     NaN  236870242  700713800  
1416      PUBLIC   False     NaN  236870242  700713800  
1417      PUBLIC   False  

Any other changes would depend on what's needed for the project, and that is already covered in it's respective report